In [1]:
import pandas as pd
import numpy as np

#Data summarization tool
import pandas_profiling as pp

#Visualization tools
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

#Input missing values with MICE 
from impyute.imputation.cs import mice

## Import standard scaler and standardize all numeric variables(which are not target variables)
from sklearn.preprocessing import StandardScaler

#Warning suppression
import warnings
warnings.filterwarnings('ignore')

#Model tuning tools
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split, KFold, GridSearchCV 
from sklearn.model_selection import cross_val_score, learning_curve
from sklearn.metrics import mean_squared_error

#Regression Algorithm 
from sklearn.svm import SVR
from sklearn.ensemble import ExtraTreesRegressor, RandomForestRegressor, GradientBoostingRegressor
from sklearn.linear_model import LinearRegression

import xgboost as xgb
import lightgbm as lgb

sns.set(style='white', context='notebook', palette='deep')

In [2]:
Train_df = pd.read_csv("train.csv")
Test_df = pd.read_csv("test.csv")
submission_sample_df = pd.read_csv("sample_submit.csv")

In [3]:
Train_df.sample(10)

galactic year                                      galaxy  \
3108        1007012                                   Boötes II   
3711        1014049                    Carina Dwarf (E206-G220)   
3595        1012036                                   Boötes II   
3145        1007012                             ESO 321-014[70]   
3185        1008016                         UGC 8508 (I Zw 060)   
615          993012                             Cas 1 (KK98 19)   
2853        1005006                    KUG 1210+301B (KK98 127)   
3344        1010025                          UGC 8651 (DDO 181)   
1282         997002                                     IC 3104   
1955        1000000  Cassiopeia Dwarf (Cas dSph, Andromeda VII)   

      existence expectancy index  existence expectancy at birth  \
3108                    0.946406                      89.428369   
3711                    0.757331                      68.584579   
3595                    1.035831                      84.013161   
3145                    0.933335                      80.920375   
3185                    1.080605                      87.584084   
615                     0.941279                      79.054532   
2853                    0.917028                      76.135408   
3344                    0.696114                      63.049280   
1282                    0.662733                      69.191241   
1955                    1.116187                      86.121512   

      Gross income per capita  Income Index  \
3108             40967.122628      0.949267   
3711             21939.604320      0.674618   
3595             27722.890109      1.004407   
3145             31265.773273      0.977339   
3185             37461.533249      1.080375   
615              17374.965101      0.827300   
2853             17403.821200      0.570047   
3344             26450.180422      0.531363   
1282             13954.208697      0.635482   
1955             57681.714317      1.090303   

      Expected years of education (galactic years)  \
3108                                     17.605656   
3711                                     13.938857   
3595                                     17.731875   
3145                                     17.657618   
3185                                     20.027302   
615                                      15.970871   
2853                                     11.337271   
3344                                      7.350506   
1282                                      8.706361   
1955                                     22.039843   

      Mean years of education (galactic years)  \
3108                                 13.612589   
3711                                  6.356593   
3595                                 12.108194   
3145                                 11.298041   
3185                                 11.755584   
615                                   6.744599   
2853                                  6.312458   
3344                                  7.790751   
1282                                  6.189593   
1955                                 12.641168   

      Intergalactic Development Index (IDI)  Education Index  ...  \
3108                               0.861028         0.971673  ...   
3711                               0.724866         0.766743  ...   
3595                               1.075783         1.015537  ...   
3145                               0.848626         0.727172  ...   
3185                               0.964757         0.821740  ...   
615                                0.878769         0.589002  ...   
2853                               0.628910         0.513015  ...   
3344                               0.636236         0.457493  ...   
1282                               0.613685         0.464295  ...   
1955                               0.959668         0.986023  ...   

      Intergalactic Development Index (IDI), female  \
3108                                            NaN

In [4]:
Test_df.sample(10)

galactic year                                       galaxy  \
343        1010025                                    Carina II   
342        1016064                 Leo II Dwarf (Leo B, DDO 93)   
461        1011030  Sagittarius Dwarf Irregular Galaxy (SagDIG)   
725        1009020                                        Leo P   
151        1010025                   Lacerta I (Andromeda XXXI)   
160        1015056                 Large Magellanic Cloud (LMC)   
330        1013042                     KUG 1210+301B (KK98 127)   
266        1008016                  Barnard's Galaxy (NGC 6822)   
24         1008016                                      KKh 060   
272        1007012                         ESO 383-087 (ISG 39)   

     existence expectancy index  existence expectancy at birth  \
343                    0.903945                      82.352492   
342                    0.903199                      81.593756   
461                    0.954096                      80.192149   
725                    1.046803                      91.522942   
151                    0.783617                      77.744213   
160                    0.790034                      79.425296   
330                    0.895482                      79.269223   
266                    0.858671                      71.787106   
24                     0.638031                      64.127677   
272                    0.862022                      70.802261   

     Gross income per capita  Income Index  \
343             19355.865948      0.577838   
342             20175.796213      0.764089   
461             41645.093076      0.823286   
725             57931.374259      1.200405   
151             40638.754101      0.937423   
160             21972.122930      0.831417   
330             27165.777125      0.684036   
266             31319.604901      0.968514   
24              31205.573019      0.831811   
272             15214.443205      0.719456   

     Expected years of education (galactic years)  \
343                                     13.780502   
342                                     14.143273   
461                                     15.763833   
725                                     19.611177   
151                                     17.499112   
160                                     17.095940   
330                                     14.838678   
266                                     14.080219   
24                                      17.587492   
272                                      9.785191   

     Mean years of education (galactic years)  \
343                                 10.370882   
342                                  9.408389   
461                                 12.735360   
725                                 13.713159   
151                                 15.630745   
160                                  6.481246   
330                                  6.792488   
266                                  8.478561   
24                                   9.030719   
272                                  7.257570   

     Intergalactic Development Index (IDI)  Education Index  ...  \
343                               0.697686         0.657446  ...   
342                               0.785611         0.809592  ...   
461                               0.852610         0.809721  ...   
725                               1.177371         1.042899  ...   
151                               0.919988         1.054276  ...   
160                               0.686543         0.597843  ...   
330                               0.700574         0.629785  ...   
266                               0.802189         0.798300  ...   
24                                0.685476         0.793508  ...   
272                               0.645459         0.568823  ...   

     Current health expenditure (% of GGP)  \
343                               4.537896   
342                               9.219633   
461                   

In [5]:
submission_sample_df.sample(10)

index  pred  opt_pred
342    342  0.08        60
800    800  0.08        10
78      78  0.08       100
367    367  0.08        60
729    729  0.08        20
224    224  0.08        70
501    501  0.08        40
779    779  0.08        20
304    304  0.08        60
716    716  0.08        20

In [6]:
# pp.ProfileReport(Train_df)

In [7]:
Train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3865 entries, 0 to 3864
Data columns (total 80 columns):
galactic year                                                                              3865 non-null int64
galaxy                                                                                     3865 non-null object
existence expectancy index                                                                 3864 non-null float64
existence expectancy at birth                                                              3864 non-null float64
Gross income per capita                                                                    3837 non-null float64
Income Index                                                                               3837 non-null float64
Expected years of education (galactic years)                                               3732 non-null float64
Mean years of education (galactic years)                                                   3502 non-null 

In [8]:
Train_df.describe()

galactic year  existence expectancy index  \
count   3.865000e+03                 3864.000000   
mean    1.000709e+06                    0.872479   
std     6.945463e+03                    0.162367   
min     9.900250e+05                    0.227890   
25%     9.950060e+05                    0.763027   
50%     1.000000e+06                    0.907359   
75%     1.006009e+06                    0.992760   
max     1.015056e+06                    1.246908   

       existence expectancy at birth  Gross income per capita  Income Index  \
count                    3864.000000              3837.000000   3837.000000   
mean                       76.798111             31633.240872      0.825154   
std                        10.461654             18736.378445      0.194055   
min                        34.244062              -126.906522      0.292001   
25%                        69.961449             20169.118912      0.677131   
50%                        78.995101             26600.768195      0.827300   
75%                        84.558971             36898.631754      0.970295   
max                       100.210053            151072.683156      1.361883   

       Expected years of education (galactic years)  \
count                                   3732.000000   
mean                                      14.723296   
std                                        3.612546   
min                                        3.799663   
25%                                       12.592467   
50%                                       14.942913   
75%                                       17.123797   
max                                       26.955944   

       Mean years of education (galactic years)  \
count                               3502.000000   
mean                                  10.283959   
std                                    3.319948   
min                                    1.928166   
25%                                    7.654169   
50%                                   10.385465   
75%                                   12.884752   
max                                   19.057648   

       Intergalactic Development Index (IDI)  Education Index  \
count                            3474.000000      3474.000000   
mean                                0.804246         0.745900   
std                                 0.176242         0.199795   
min                                 0.273684         0.189874   
25%                                 0.671862         0.597746   
50%                                 0.824758         0.761255   
75%                                 0.939043         0.893505   
max                                 1.232814         1.269625   

       Intergalactic Development Index (IDI), Rank  ...  \
count                                  3432.000000  ...   
mean                                    135.129178  ...   
std                                      52.449535  ...   
min                                       9.925906  ...   
25%                                      92.262724  ...   
50%                                     135.914318  ...   
75%                                     175.301993  ...   
max                                     278.786613  ...   

       Intergalactic Development Index (IDI), female  \
count                                     916.000000   
mean                                        0.823561   
std                                         0.185780   
min                                         0.305733   
25%                                         0.690707   
50%                                         0.835410   
75%                                         0.970365   
max                                         1.237661   

       Intergalactic Development Index (IDI), male  \
count                                   915.000000   
mean                                      0.844209   
std                                       0.159041   
min                            

In [9]:
Train_df.isna().sum()

galactic year                                                                   0
galaxy                                                                          0
existence expectancy index                                                      1
existence expectancy at birth                                                   1
Gross income per capita                                                        28
                                                                             ... 
Adjusted net savings                                                         2953
Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total    2924
Private galaxy capital flows (% of GGP)                                      2991
Gender Inequality Index (GII)                                                3021
y                                                                               0
Length: 80, dtype: int64

In [10]:
-np.log(20)

-2.995732273553991

In [11]:
train_clean_df = Train_df.dropna(axis=1, thresh=1500)
train_clean_df.isna().sum()

galactic year                                                     0
galaxy                                                            0
existence expectancy index                                        1
existence expectancy at birth                                     1
Gross income per capita                                          28
Income Index                                                     28
Expected years of education (galactic years)                    133
Mean years of education (galactic years)                        363
Intergalactic Development Index (IDI)                           391
Education Index                                                 391
Intergalactic Development Index (IDI), Rank                     433
Population using at least basic drinking-water services (%)    1844
Population using at least basic sanitation services (%)        1850
Gross capital formation (% of GGP)                             2363
y                                               

In [12]:
clean_data_df = train_clean_df.dropna(axis=1, thresh=1932)
clean_data_df.isna().sum()

galactic year                                                     0
galaxy                                                            0
existence expectancy index                                        1
existence expectancy at birth                                     1
Gross income per capita                                          28
Income Index                                                     28
Expected years of education (galactic years)                    133
Mean years of education (galactic years)                        363
Intergalactic Development Index (IDI)                           391
Education Index                                                 391
Intergalactic Development Index (IDI), Rank                     433
Population using at least basic drinking-water services (%)    1844
Population using at least basic sanitation services (%)        1850
y                                                                 0
dtype: int64

In [13]:
# pp.ProfileReport(clean_data_df)

In [14]:
le = LabelEncoder()

In [15]:
encoded_galaxy = le.fit_transform(clean_data_df.galaxy)
encoded_galaxy.max()

180

In [16]:
mice_data_df = clean_data_df.drop(columns=['galaxy',
       'Population using at least basic drinking-water services (%)',
       'Population using at least basic sanitation services (%)'])
mice_data_df.sample(5)

galactic year  existence expectancy index  \
2602        1004004                    1.029299   
214          991020                    0.872802   
857          994009                    1.088493   
2685        1004004                    0.754786   
2923        1006009                    1.059927   

      existence expectancy at birth  Gross income per capita  Income Index  \
2602                      86.922955             79692.842508      1.134474   
214                       77.835498             26628.104226      0.705495   
857                       83.170006             52143.105646      1.079667   
2685                      68.231464             16744.574843      0.532862   
2923                      88.481634             27913.112035      0.910309   

      Expected years of education (galactic years)  \
2602                                     22.745031   
214                                      12.045568   
857                                      15.502207   
2685                                     12.361786   
2923                                     19.399827   

      Mean years of education (galactic years)  \
2602                                 18.050698   
214                                   8.424414   
857                                  11.405274   
2685                                 10.836160   
2923                                 16.120011   

      Intergalactic Development Index (IDI)  Education Index  \
2602                               1.116340         1.103276   
214                                0.810689         0.666019   
857                                0.915467         0.816477   
2685                               0.574918         0.567620   
2923                               1.075726         1.081280   

      Intergalactic Development Index (IDI), Rank         y  
2602                                    46.475035  0.296728  
214                                    128.521265  0.060906  
857                                     73.413562  0.154210  
2685                                   201.333134  0.046615  
2923                                    58.008703  0.228610

In [17]:
scaler=StandardScaler()
feature_scaled = scaler.fit_transform(mice_data_df.drop(columns = ['y']))
feature_scaled= pd.DataFrame(data = feature_scaled, columns = mice_data_df.drop(columns = ['y']).columns)
# feature_scaled["y"] = mice_data_df['y']
feature_scaled.sample(10)

galactic year  existence expectancy index  \
2911       0.763178                   -0.148182   
2735       0.618749                    0.160240   
2096       0.041895                   -0.003428   
1399      -0.533807                   -0.910780   
1472      -0.389954                   -0.154689   
1989       0.041895                    0.132912   
2035       0.041895                    0.380163   
2167       0.186036                    0.530783   
69        -1.538478                   -0.058174   
1957      -0.102103                   -0.204960   

      existence expectancy at birth  Gross income per capita  Income Index  \
2911                       0.285633                -0.293666     -0.467555   
2735                       0.692830                 0.189414      0.876605   
2096                      -0.428774                -0.427118      0.414777   
1399                      -0.498673                -0.722034     -1.150320   
1472                       0.684438                -0.512843     -0.087246   
1989                       0.526278                 0.312755      0.995895   
2035                       0.524191                -0.987823     -0.532346   
2167                       0.142041                 0.034449     -0.158155   
69                        -0.325605                -0.852249      0.060218   
1957                       0.048370                -0.724454     -0.807830   

      Expected years of education (galactic years)  \
2911                                      1.194477   
2735                                      0.964589   
2096                                      0.821124   
1399                                     -1.123604   
1472                                      0.043722   
1989                                      1.316728   
2035                                      0.775133   
2167                                     -0.045541   
69                                        0.521014   
1957                                     -1.707966   

      Mean years of education (galactic years)  \
2911                                 -0.013376   
2735                                  1.757410   
2096                                  0.511671   
1399                                 -0.444077   
1472                                  1.544042   
1989                                  1.145489   
2035                                  0.880934   
2167                                  0.332136   
69                                         NaN   
1957                                 -1.332150   

      Intergalactic Development Index (IDI)  Education Index  \
2911                               0.354335        -0.032097   
2735                               0.620034         1.404818   
2096                               0.066785         0.901697   
1399                              -0.734452        -1.548399   
1472                               0.116845         0.564702   
1989                               0.952741         1.031068   
2035                               0.144030         0.537225   
2167                              -0.423277         0.404365   
69                                      NaN              NaN   
1957                              -1.360896        -1.310514   

      Intergalactic Development Index (IDI), Rank  
2911                                     1.362479  
2735                                    -0.659738  
2096                                    -0.089427  
1399                                     0.658757  
1472                                    -0.128978  
1989                                    -0.905577  
2035                                     0.483414  
2167                                     0.264172  
69                                            NaN  
1957                                     0.881389

In [18]:
# start the MICE training
imputed_training=mice(feature_scaled)

In [19]:
imputed_training.sample(10)

0         1         2         3         4         5         6  \
1733 -0.246100  0.724883  0.481439 -0.283139  0.685998  0.329734 -0.061960   
3060  0.763178  0.458670  1.020154  0.649723  0.965293  1.186012  1.290130   
566  -1.108357 -1.540140 -1.494042 -0.943151 -0.752876 -1.115901 -1.080337   
1064 -0.821226 -3.002315 -2.888294 -0.812718 -1.953639 -1.974032 -1.224216   
1427 -0.533807 -0.516084 -0.278989 -0.465591 -0.526891 -1.138999 -0.087920   
239  -1.395201 -0.394295 -0.591594 -0.439413 -0.615564 -0.622551 -0.601833   
1950 -0.102103 -0.026412 -0.347294 -0.694660 -0.105204 -0.749578 -0.495308   
2527  0.474463  0.500123  0.717104 -0.192973  0.435591  0.131851  0.282124   
53   -1.538478  0.799929  0.235473 -0.146862 -0.316557 -0.675175 -0.285054   
1923 -0.102103  1.006597  0.732801  0.682152  0.952332  0.603849  0.071556   

             7         8         9  
1733  0.861756 -0.230022 -0.711151  
3060  0.826079  2.163587 -0.917118  
566  -1.274239 -1.163670  0.829046  
1064 -2.283226 -1.640817  1.245824  
1427 -0.551265 -0.016116  0.363318  
239  -0.386167 -0.384915 -0.198640  
1950 -0.458247 -0.589006  0.427949  
2527  0.482891  0.281809 -0.038471  
53   -0.630405 -1.058720  0.404972  
1923  0.347164  0.765603 -0.847337

In [20]:
imputed_training.columns = mice_data_df.drop(columns = ['y']).columns


In [21]:
pp.ProfileReport(imputed_training)

In [22]:
imputed_training.sample(10)

galactic year  existence expectancy index  \
1304      -0.533807                   -1.316632   
1496      -0.389954                    0.114344   
684       -1.108357                   -1.482495   
294       -1.395201                   -1.033780   
2580       0.474463                    0.996967   
3372       1.341472                    1.135550   
430       -1.251779                   -3.593252   
2219       0.186036                   -1.398855   
3566       1.631051                    1.602644   
2095       0.041895                   -0.226240   

      existence expectancy at birth  Gross income per capita  Income Index  \
1304                      -2.091962                -0.607916     -1.674394   
1496                       0.988401                -0.346643      0.776605   
684                       -1.075860                -0.315663     -1.050645   
294                       -0.342141                -0.351513     -1.001215   
2580                       0.632216                 0.219129      0.194114   
3372                       1.169597                 0.675481      1.428370   
430                       -3.838196                -0.230973     -1.809192   
2219                      -1.270884                -0.510679     -1.798616   
3566                       0.914224                 2.404334      1.352395   
2095                       0.785984                -0.037957      0.675852   

      Expected years of education (galactic years)  \
1304                                     -2.329643   
1496                                      0.251608   
684                                      -0.709536   
294                                      -1.721667   
2580                                      0.391296   
3372                                      1.165687   
430                                      -1.697001   
2219                                     -1.941166   
3566                                      1.791080   
2095                                     -0.485624   

      Mean years of education (galactic years)  \
1304                                 -1.858215   
1496                                  1.374386   
684                                  -1.405001   
294                                  -1.777803   
2580                                  0.754466   
3372                                  0.988442   
430                                  -1.704737   
2219                                 -1.138112   
3566                                  1.598970   
2095                                 -0.794553   

      Intergalactic Development Index (IDI)  Education Index  \
1304                              -2.036344        -2.099207   
1496                               0.817346         0.848064   
684                               -2.103633        -1.217010   
294                               -1.317927        -1.953509   
2580                               0.725634         0.544182   
3372                               1.637461         1.864284   
430                               -1.937827        -1.539646   
2219                              -2.511923        -2.483041   
3566                               1.723318         1.392241   
2095                               0.471218        -0.583748   

      Intergalactic Development Index (IDI), Rank  
1304                                     1.673883  
1496                                    -0.862144  
684                                      0.867479  
294                                      0.654774  
2580                                    -0.491789  
3372                                    -0.847785  
430                                      1.120243  
2219                                     1.671954  
3566                                    -1.802788  
2095                                     0.546605

In [23]:
train_df = imputed_training
y = mice_data_df['y']

In [24]:
X_train, X_test, y_train, y_test = train_test_split(train_df, y, test_size=0.2, shuffle=True)
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(3092, 10) (773, 10) (3092,) (773,)


In [25]:
rs = 3
kfold = KFold(n_splits=10, random_state=rs, shuffle=True)

regressors = []
regressors.append(SVR())
regressors.append(GradientBoostingRegressor(random_state=rs))
regressors.append(ExtraTreesRegressor(n_estimators=rs))
regressors.append(RandomForestRegressor(random_state=rs))
regressors.append(xgb.XGBRegressor(random_state=rs, objective="reg:squarederror"))
regressors.append(lgb.LGBMRegressor(random_state=rs))

cv_results = []
for regressor in regressors:     #scores to be minimised are negated (neg)
    cv_results.append(np.sqrt(abs(cross_val_score(regressor, X_train, y=y_train, scoring='neg_mean_squared_error', cv=kfold))))

cv_means = []
cv_stds = []
for cv_result in cv_results:
    cv_means.append(cv_result.mean())
    cv_stds.append(cv_result.std())
    
cv_res = pd.DataFrame({ 
    "Algorithm": ["SVR", "GBR", "EXR", "RFR", "XGBR", "LGBM"],
    "CrossValMeans": cv_means, "CrossValErrors": cv_stds
                       })
cv_res = cv_res.sort_values("CrossValMeans", ascending=True)
print(cv_res)

  Algorithm  CrossValMeans  CrossValErrors
1       GBR       0.031314        0.004459
4      XGBR       0.031542        0.004957
5      LGBM       0.031676        0.005200
3       RFR       0.032893        0.005346
2       EXR       0.034782        0.004482
0       SVR       0.056283        0.003973


In [26]:
gbr = GradientBoostingRegressor(random_state=rs)
xgbr = xgb.XGBRegressor(random_state=rs, objective="reg:squarederror")
lgbm = lgb.LGBMRegressor(random_state=rs)
rfr = RandomForestRegressor(random_state=rs)
exr = ExtraTreesRegressor(n_estimators=rs)
svr = SVR()


In [27]:
trainedmodelgbr = gbr.fit(X_train,y_train)
trainedmodelxgbr = xgbr.fit(X_train,y_train)
trainedmodellgbm = lgbm.fit(X_train,y_train)
trainedmodelrfr = rfr.fit(X_train,y_train)
trainedmodelexr = exr.fit(X_train,y_train)
trainedmodelsvr = svr.fit(X_train,y_train)

In [28]:
y_pred = trainedmodelgbr.predict(X_test)
print("GBR", mean_squared_error(y_pred, y_test))
y_pred = trainedmodelxgbr.predict(X_test)
print("XGBR", mean_squared_error(y_pred, y_test))
y_pred = trainedmodellgbm.predict(X_test)
print("LGBM", mean_squared_error(y_pred, y_test))
y_pred = trainedmodelrfr.predict(X_test)
print("RFR", mean_squared_error(y_pred, y_test))
y_pred = trainedmodelexr.predict(X_test)
print("EXR", mean_squared_error(y_pred, y_test))
y_pred = trainedmodelsvr.predict(X_test)
print("SVR", mean_squared_error(y_pred, y_test))

GBR 0.0011354837853015508
XGBR 0.0011279754723409587
LGBM 0.0009514173896435464
RFR 0.0010145785328526677
EXR 0.0015573116511727824
SVR 0.003244401164749733


In [29]:
testData = Test_df[imputed_training.columns]
testData.sample(5)

galactic year  existence expectancy index  existence expectancy at birth  \
853        1015056                    1.131963                      89.417510   
514        1012036                    0.976022                      84.534550   
476        1007012                    0.960905                      81.032314   
49         1015056                    0.671839                      68.143825   
881        1009020                    1.173076                      89.891307   

     Gross income per capita  Income Index  \
853             66881.425967      1.156961   
514             67130.941116      1.129016   
476             39866.366342      0.981671   
49              44345.751126      1.041028   
881             61968.904515      0.956639   

     Expected years of education (galactic years)  \
853                                     20.638518   
514                                     20.691698   
476                                     16.245241   
49                                      11.042017   
881                                     18.975100   

     Mean years of education (galactic years)  \
853                                 13.677196   
514                                 17.854808   
476                                 12.943035   
49                                   8.754920   
881                                 14.623960   

     Intergalactic Development Index (IDI)  Education Index  \
853                               0.989646         1.068227   
514                               1.032070         1.119825   
476                               0.952490         0.847697   
49                                0.755132         0.642207   
881                               1.009860         1.051840   

     Intergalactic Development Index (IDI), Rank  
853                                    59.899568  
514                                    81.118351  
476                                   111.080402  
49                                    210.817584  
881                                    74.392430

In [33]:
test_feature_scaled = scaler.fit_transform(testData)
test_feature_scaled= mice(pd.DataFrame(data = test_feature_scaled, columns = testData.columns))
test_feature_scaled.columns = testData.columns
test_feature_scaled.sample(10)

galactic year  existence expectancy index  existence expectancy at birth  \
592      -0.860345                    0.548999                       0.639084   
516      -1.557595                    0.395353                       0.642037   
850       0.536238                    1.502550                       0.911029   
136       0.536238                   -1.117553                      -1.039180   
252       1.235572                   -0.542069                      -1.654514   
754      -1.557595                    1.032002                       0.054148   
31       -1.557595                   -2.039071                      -1.284307   
163       1.585585                   -0.980945                      -1.071438   
609       1.235572                    0.584495                       0.574089   
384      -0.162401                   -0.006327                      -0.591558   

     Gross income per capita  Income Index  \
592                 0.036451     -0.019847   
516                -0.941435     -1.187647   
850                 1.169100      0.924612   
136                -1.017693     -1.495990   
252                -1.157586     -1.957643   
754                -0.406722     -0.396201   
31                 -1.022532     -1.078621   
163                -0.638966     -1.197556   
609                -0.622247     -0.919664   
384                -0.813931     -1.698916   

     Expected years of education (galactic years)  \
592                                      0.704812   
516                                     -0.392531   
850                                      2.000658   
136                                     -0.051410   
252                                     -0.979480   
754                                      0.335051   
31                                      -1.573648   
163                                     -1.034188   
609                                     -0.813714   
384                                     -0.426741   

     Mean years of education (galactic years)  \
592                                  0.848149   
516                                 -0.647371   
850                                  0.837435   
136                                 -0.605754   
252                                 -1.369307   
754                                  0.291101   
31                                  -2.312443   
163                                 -1.414850   
609                                 -0.587227   
384                                 -1.686448   

     Intergalactic Development Index (IDI)  Education Index  \
592                              -0.468643         0.561434   
516                              -1.211584        -0.616403   
850                               0.870873         1.154526   
136                              -1.143871        -0.692867   
252                              -1.260395        -0.687592   
754                               0.586371         0.198367   
31                               -1.833577        -2.377801   
163                              -1.409192        -1.364850   
609                              -0.736806        -0.540765   
384                              -0.274233        -1.540599   

     Intergalactic Development Index (IDI), Rank  
592                                    -0.543654  
516                                     0.322303  
850                                    -1.741312  
136                                     1.424952  
252                                     1.481054  
754                                     0.058103  
31                                      1.755884  
163                                     1.771669  
609                                     0.854937  
384                                     1.301531

In [34]:
y_pred1 = trainedmodelgbr.predict(test_feature_scaled)
y_pred2 = trainedmodelxgbr.predict(test_feature_scaled)
y_pred3 = trainedmodellgbm.predict(test_feature_scaled)
y_pred4 = trainedmodelrfr.predict(test_feature_scaled)
y_pred5 = trainedmodelexr.predict(test_feature_scaled)
y_pred6 = trainedmodelsvr.predict(test_feature_scaled)

In [59]:
Train_df.loc[Train_df["galaxy" ] == "Leo P"]

galactic year galaxy  existence expectancy index  \
12           990025  Leo P                    1.068957   
348          991020  Leo P                    0.934927   
460          992016  Leo P                    1.000826   
584          993012  Leo P                    1.018948   
878          994009  Leo P                    1.048111   
1030         995006  Leo P                    0.958981   
1251         996004  Leo P                    1.150250   
1308         997002  Leo P                    1.105523   
1464         998001  Leo P                    1.074646   
1734         999000  Leo P                    1.048917   
1880        1000000  Leo P                    0.981500   
2143        1001000  Leo P                    0.970342   
2242        1002001  Leo P                    1.049054   
2431        1003002  Leo P                    1.070496   
2576        1004004  Leo P                    1.140043   
2819        1005006  Leo P                    1.143908   
2901        1006009  Leo P                    1.138901   
3573        1012036  Leo P                    1.092363   
3664        1013042  Leo P                    1.036482   
3773        1014049  Leo P                    1.043486   
3794        1015056  Leo P                    1.014391   

      existence expectancy at birth  Gross income per capita  Income Index  \
12                        90.854092             48579.590188      1.082535   
348                       84.373655             53556.906106      1.120308   
460                       93.955119             55717.265289      1.010462   
584                       85.078377             50753.836514      1.120491   
878                       90.214493             52670.656452      1.053284   
1030                      87.054244             52985.767198      1.004742   
1251                      87.438512             39947.642346      1.044112   
1308                      89.607899             62258.655175      1.178641   
1464                      89.644665             64748.027781      1.124437   
1734                      88.828308             64334.784697      1.069713   
1880                      84.314738             63783.893769      1.211279   
2143                      85.665585             55756.052849      1.036512   
2242                      85.921768             63325.021184      1.080763   
2431                      84.546586             54102.213240      1.164459   
2576                      89.635655             53306.023474      1.181349   
2819                      90.298398             62027.777855      1.141550   
2901                      83.948817             68701.732203      1.031044   
3573                      91.415537             68039.634174      1.158418   
3664                      86.818277             53982.656296      1.088095   
3773                      91.105042             69235.296937      1.126078   
3794                      89.360791             60967.192686      1.190086   

      Expected years of education (galactic years)  \
12                                       17.459732   
348                                      16.722023   
460                                      18.996268   
584                                      16.659388   
878                                      22.179132   
1030                                     20.684727   
1251                                     21.254146   
1308                                     20.345008   
1464                                     20.236569   
1734                                     19.679865   
1880                                     19.951256   
2143                                     17.007742   
2242                                     20.714647   
2431                                     19.556645   
2576                                     20.781861   
2819                                     19.539466   
2901                                     19.398722   
3573                                    

In [30]:
Test_df.isna().sum()

galactic year                                                                  0
galaxy                                                                         0
existence expectancy index                                                     5
existence expectancy at birth                                                  5
Gross income per capita                                                        5
                                                                            ... 
Intergalactic Development Index (IDI), male, Rank                            341
Adjusted net savings                                                         371
Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total    408
Private galaxy capital flows (% of GGP)                                      354
Gender Inequality Index (GII)                                                361
Length: 79, dtype: int64

In [32]:
Test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 890 entries, 0 to 889
Data columns (total 79 columns):
galactic year                                                                              890 non-null int64
galaxy                                                                                     890 non-null object
existence expectancy index                                                                 885 non-null float64
existence expectancy at birth                                                              885 non-null float64
Gross income per capita                                                                    885 non-null float64
Income Index                                                                               885 non-null float64
Expected years of education (galactic years)                                               885 non-null float64
Mean years of education (galactic years)                                                   882 non-null float64
In

In [110]:
def allocate_energy(df):
    y_pred1= df["pred"]
    existence_index =  df["existence expectancy index"]
#     print("Ypred", y_pred1)
    extra_energy = 50000
    max_energy_allocation = 100
    min_energy_allocation = 0
    low_existence_index_mark = 0.7
#     if existence_index < low_existence_index_mark:
#         extra_energy = 0.1*50000
# #         print("Extra Energy ", extra_energy)
#     else:
#         extra_energy = 0.9*50000

    index_increase_potential = -(np.log(y_pred1+0.01)+3)

    index_increase_likelihood = (extra_energy * index_increase_potential **2) / 1000
#     print("Index increase likelihood ",index_increase_likelihood)


    if index_increase_likelihood> max_energy_allocation:
        galaxy_energy_allocation = 100
    elif index_increase_likelihood < min_energy_allocation:
        galaxy_energy_allocation = 0
    else:
        galaxy_energy_allocation = index_increase_likelihood

#     print("Galaxy energy allocation",galaxy_energy_allocation)
    return galaxy_energy_allocation

In [111]:
y = 0
t_df = Test_df
for x in [y_pred1,y_pred2,y_pred3,y_pred4,y_pred5,y_pred6]:
    t_df["pred"] = x  
#     print(t_df.sample(5))
    sub_df = pd.DataFrame(data=x,columns=["pred"])
    
    sub_df["opt_pred"] = t_df.apply(allocate_energy, axis = 1)
#     print(sub_df.sample(10))
#     break
    sub_df.to_csv(path_or_buf="submission"+str(y),index= True, index_label= "index")
    y+=1

In [91]:
sub_df.sample(10)

pred    opt_pred
23   0.040605   17.902321
841  0.175857  100.000000
581  0.057349  100.000000
774  0.183781  100.000000
730  0.239369  100.000000
247  0.050460  100.000000
560  0.114806  100.000000
557  0.087353  100.000000
543  0.070931  100.000000
197  0.047690  100.000000

In [76]:
df = pd.DataFrame([{'c1':10, 'c2':100}, {'c1':11,'c2':110}, {'c1':12,'c2':120}])
df

c1   c2
0  10  100
1  11  110
2  12  120

In [77]:
for index, row in df.iterrows():
    row["c3"] = row['c1']+row['c2']
    print(df)
    print(row['c1'],row['c2'], row["c3"])

   c1   c2
0  10  100
1  11  110
2  12  120
10 100 110
   c1   c2
0  10  100
1  11  110
2  12  120
11 110 121
   c1   c2
0  10  100
1  11  110
2  12  120
12 120 132


In [107]:
-(np.log(0.5+0.01)+3)

-2.3266554467362344

In [103]:
Index

3.6733445532637656